In [1]:
import openai
import tiktoken
import tempfile
import IPython
import enum
import structlog
from gtts import gTTS
import datetime as dt
import requests
import concurrent.futures
import base64
from github import Github
import os
import re
import retrying
from xml.dom import minidom
from xml.etree import ElementTree as ET
import requests
from bs4 import BeautifulSoup
logger = structlog.getLogger()
openai.api_key = os.environ.get("OPENAI_KEY", None) or open('/Users/jong/.openai_key').read().strip()

In [2]:
class ElevenLabsTTS:
    WOMAN = 'EXAVITQu4vr4xnSDxMaL'
    MAN = 'VR6AewLTigWG4xSOukaG'
    BRIT_WOMAN = 'jnBYJClnH7m3ddnEXkeh'
    def __init__(self, api_key_fpath='/Users/jong/.elevenlabs_apikey', voice_id=None):
        with open(api_key_fpath) as f:
            self.api_key = f.read().strip()
        self._voice_id = voice_id or self.WOMAN
        self.uri = "https://api.elevenlabs.io/v1/text-to-speech/" + self._voice_id
        
    @retrying.retry(stop_max_attempt_number=5, wait_fixed=2000)
    def tts(self, text):
        headers = {
            "accept": "audio/mpeg",
            "xi-api-key": self.api_key,
        }
        payload = {
            "text": text,
        }
        return requests.post(self.uri, headers=headers, json=payload).content

In [35]:
class GttsTTS:
    WOMAN = 'us'
    MAN   = 'co.in'
    def __init__(self, voice_id=None):
        self.tld = voice_id

    @retrying.retry(stop_max_attempt_number=5, wait_fixed=2000)
    def tts(self, text):
        speech = gTTS(text=text, lang='en', tld=self.tld, slow=False)
        with tempfile.NamedTemporaryFile(delete=True) as fp:
            temp_filename = fp.name
            speech.save(temp_filename)
            with open(temp_filename, 'rb') as f:
                audio_data = f.read()
        return audio_data

In [3]:
class Chat:
    class Model(enum.Enum):
        GPT3_5 = "gpt-3.5-turbo"
        GPT_4  = "gpt-4"

    def __init__(self, system, max_length=4096//2):
        self._system = system
        self._max_length = max_length
        self._history = [
            {"role": "system", "content": self._system},
        ]

    @classmethod
    def num_tokens_from_text(cls, text, model="gpt-3.5-turbo"):
        """Returns the number of tokens used by some text."""
        encoding = tiktoken.encoding_for_model(model)
        return len(encoding.encode(text))
    
    @classmethod
    def num_tokens_from_messages(cls, messages, model="gpt-3.5-turbo"):
        """Returns the number of tokens used by a list of messages."""
        encoding = tiktoken.encoding_for_model(model)
        num_tokens = 0
        for message in messages:
            num_tokens += 4  # every message follows <im_start>{role/name}\n{content}<im_end>\n
            for key, value in message.items():
                num_tokens += len(encoding.encode(value))
                if key == "name":  # if there's a name, the role is omitted
                    num_tokens += -1  # role is always required and always 1 token
        num_tokens += 2  # every reply is primed with <im_start>assistant
        return num_tokens

    @retrying.retry(stop_max_attempt_number=5, wait_fixed=2000)
    def _msg(self, *args, model=Model.GPT3_5.value, **kwargs):
        return openai.ChatCompletion.create(
            *args,
            model=model,
            messages=self._history,
            **kwargs
        )
    
    def message(self, next_msg=None, **kwargs):
        # TODO: Optimize this if slow through easy caching
        while len(self._history) > 1 and self.num_tokens_from_messages(self._history) > self._max_length:
            logger.info(f'Popping message: {self._history.pop(1)}')
        if next_msg is not None:
            self._history.append({"role": "user", "content": next_msg})
        logger.info('requesting openai...')
        resp = self._msg(**kwargs)
        logger.info('received openai...')
        text = resp.choices[0].message.content
        self._history.append({"role": "assistant", "content": text})
        return text

In [4]:
class PodcastChat(Chat):
    def __init__(self, topic, podcast="award winning NPR", max_length=4096//2, hosts=['Tom', 'Jen'], host_voices=[GttsTTS(GttsTTS.MAN), GttsTTS(GttsTTS.WOMAN)]):
        system = f"You are an {podcast} podcast with hosts {hosts[0]} and {hosts[1]}."
        super().__init__(system, max_length=max_length)
        self._podcast = podcast
        self._topic = topic
        self._hosts = hosts
        self._history.append({
            "role": "user", "content": f"Generate an informative and entertaining podcast episode about {topic}. Make sure to teach complex topics in an intuitive way."
        })
        self._tts_h1, self._tts_h2 = host_voices

    def text2speech(self, text, spacing_ms=350):
        tmpdir = '/tmp'
        with concurrent.futures.ThreadPoolExecutor(max_workers=10) as thread_pool:
            i = 0
            jobs = []
            def write_audio(msg, i, voice, **kwargs):
                logger.info(f'requesting tts {i=}')
                s = voice.tts(msg)
                logger.info(f'received tts {i=}')
                return s

            text = text.replace('\n', '!!!LINEBREAK!!!').replace('\\', '').replace('"', '')
            # Build text one at a time
            currline, currname = "", self._hosts[0]
            name2tld = {self._hosts[0]: 'co.uk', self._hosts[1]: 'com'}
            name2voice = {self._hosts[0]: self._tts_h1, self._hosts[1]: self._tts_h2}
            audios = []
            for line in text.split("!!!LINEBREAK!!!"):
                if not line.strip(): continue
                if line.startswith(f"{self._hosts[0]}: ") or line.startswith(f"{self._hosts[1]}: "):
                    if currline:
                        jobs.append(thread_pool.submit(write_audio, currline, i, name2voice[currname], lang='en', tld=name2tld[currname]))
                        i += 1
                    currline = line[4:]
                    currname = line[:3]
                else:
                    currline += line
            if currline:
                jobs.append(thread_pool.submit(write_audio, currline, i, name2voice[currname], lang='en', tld=name2tld[currname]))
                i+=1
            # Concat files
            audios = [b''] * len(jobs)
            for future in concurrent.futures.as_completed(jobs):
                idx = jobs.index(future)
                audios[idx] = future.result()
            logger.info('concatting audio')
            audio = b''.join(audios)
            logger.info('done with audio!')
            IPython.display.display(IPython.display.Audio(audio, autoplay=False))
            return audio
            
    def step(self, msg=None, skip_aud=False, ret_aud=True, **kwargs):
        msg = self.message(msg, **kwargs)
        if skip_aud: return msg
        aud = self.text2speech(msg)
        if ret_aud: return msg, aud
        return msg

In [5]:
class PodcastRSSFeed:
    """Class to handle rss feed operations using github pages."""

    def __init__(self, org, repo, xml_path):
        self.org = org
        self.repo = repo
        self.xml_path = xml_path
        self.local_xml_path = self.download_podcast_xml()

    def get_file_base64(self, file_path):
        with open(file_path, 'rb') as file:
            return base64.b64encode(file.read()).decode('utf-8')

    def download_podcast_xml(self):
        outfile = tempfile.NamedTemporaryFile().name + '.xml'
        raw_url = f'https://raw.githubusercontent.com/{self.org}/{self.repo}/main/{self.xml_path}'
        response = requests.get(raw_url)
        print(raw_url)
        if response.status_code != 200:
            raise Exception(response.text)
        with open(outfile, 'wb') as file:
            file.write(response.content)
        return outfile

    def update_podcast_xml(self, xml_data, file_name, episode_title, episode_description, file_length):
        # Parse XML
        root = ET.fromstring(xml_data)
        channel = root.find('channel')

        file_extension = os.path.splitext(file_name)[-1].lower()[1:]
        content_type = 'audio/' + file_extension
        
        # Add new episode
        item = ET.SubElement(channel, 'item')
        ET.SubElement(item, 'title').text = episode_title
        ET.SubElement(item, 'description').text = episode_description
        ET.SubElement(item, 'pubDate').text = dt.datetime.now().strftime('%a, %d %b %Y %H:%M:%S GMT')
        ET.SubElement(item, 'enclosure', {
            'url': f'https://{self.org}.github.io/{file_name}',
            'type': content_type,
            'length': str(file_length),
        })

        # Convert back to string and pretty-format
        pretty_xml = minidom.parseString(ET.tostring(root)).toprettyxml(indent='  ')
        # Remove extra newlines
        pretty_xml = os.linesep.join([s for s in pretty_xml.splitlines() if s.strip()])
        return pretty_xml
    
    def upload_episode(self, file_path, file_name, episode_title, episode_description):
        # Authenticate with GitHub
        token = os.environ.get("GH_KEY", None) or open("/Users/jong/.gh_token").read().strip()
        gh = Github(token)

        # Get the repository
        try:
            repo = gh.get_user().get_repo(self.repo)
        except:
            repo = gh.get_organization(self.org).get_repo(self.repo)

        # Upload the audio file
        podsha = None
        try:
            podsha = repo.get_contents(file_name).sha
        except:
            pass
        with open(file_path, 'rb') as audio_file:
            audio_data = audio_file.read()
            self.upload_to_github(file_name, audio_data, f'Upload new episode: {file_name}', podsha)

        # Update and upload the podcast.xml file
        file_length = os.path.getsize(file_path)
        podcast_xml = repo.get_contents(self.xml_path)
        xml_data = base64.b64decode(podcast_xml.content).decode('utf-8')
        xml_data = self.update_podcast_xml(xml_data, file_name, episode_title, episode_description, file_length)
        self.upload_to_github(self.xml_path, xml_data, f'Update podcast.xml with new episode: {file_name}', podcast_xml.sha)

    def upload_to_github(self, file_name, file_content, commit_message, sha=None):
        # Prepare API request headers
        token = os.environ.get("GH_KEY", None) or open("/Users/jong/.gh_token").read().strip()
        gh = Github(token)
        # Get the repository
        try:
            repo = gh.get_user().get_repo(self.repo)
        except:
            repo = gh.get_organization(self.org).get_repo(self.repo)

        if sha:
            repo.update_file(file_name, commit_message, file_content, sha)
        else:
            repo.create_file(file_name, commit_message, file_content)

In [6]:
class Episode:
    def __init__(self, episode_type='narration', podcast_args=("JonathanGrant", "jonathangrant.github.io", "podcasts/podcast.xml"), **chat_kwargs):
        """
        Kinds of episodes:
            pure narration - simple TTS
            simple podcast - Text to Podcast
            complex podcast?
        """
        self.episode_type = episode_type
        self.chat = PodcastChat(**chat_kwargs)
        self.chat_kwargs = chat_kwargs
        self.pod = PodcastRSSFeed(*podcast_args)
        self.sounds = []
        self.texts = []

    def get_outline(self, n, topic=None):
        if topic is None: topic = self.chat._topic
        chat = Chat(f"You are PodcastGPT. Generate chapters for a podcast topic. The podcast is {self.chat._podcast}")
        resp = chat.message(f'Write the outline for a podcast about {topic} involving {n} parts. Just return the ordered list of parts and nothing else. Do not include a conclusion or intro.')
        chapter_pattern = re.compile(r'\d+\.\s+.*')
        chapters = chapter_pattern.findall(resp)
        if not chapters:
            logger.warning(f'Could not parse message for chapters! Message:\n{resp}')
        return chapters

    def step(self, msg=None, nparts=3):
        include = f" Remember to respond with the hosts names like {self.chat._hosts[0]}: and {self.chat._hosts[1]}:"
        msg = msg or self.chat._topic
        if self.episode_type == 'narration':
            outline = self.get_outline(msg, nparts)
            logger.info(f"Outline: {outline}")
            intro_txt, intro_aud = self.chat.step(f"Write the intro for a podcast about {msg}. The outline for the podcast is {', '.join(outline)}. Only write the introduction.{include}")
            self.sounds.append(intro_aud)
            self.texts.append(intro_txt)
            # Get parts
            for part in outline:
                logger.info(f"Part: {part}")
                part_txt, part_aud = self.chat.step(f"Write the next part: {part}.{include}")
                self.sounds.append(part_aud)
                self.texts.append(part_txt)
            # Get conclusion
            logger.info("Conclusion")
            part_txt, part_aud = self.chat.step(f"Write the conclusion. Remember, the outline was: {', '.join(outline)}.{include}")
            self.sounds.append(part_aud)
            self.texts.append(part_txt)
        elif self.episode_type == 'pure_tts':
            outline = None
            audio = self.chat.text2speech("\n".join([self.chat._hosts[i%2]+": "+x for i,x in enumerate(msg)]))
            self.sounds.append(audio)
            self.texts.extend(msg)
        return outline, '\n'.join(self.texts)

    def upload(self, title, descr):
        title_small = title.lower().replace(" ", "_")
        with tempfile.TemporaryDirectory() as tmpdir:
            tmppath = os.path.join(tmpdir, "audio_file.mp3")
            with open(tmppath, "wb") as f:
                f.write(b''.join(self.sounds))
            self.pod.upload_episode(tmppath, f"podcasts/audio/{title_small}.mp3", title, descr)



In [21]:
# %%time
# ep = Episode(episode_type='narration', topic="Logitechs 5 Year Plan to $10B in Revenue by Building Products in Computer Peripherals, Gaming, and Video Collaboration With AI")
# outline, txt = ep.step(nparts=3)
# ep.upload(ep.chat._topic, '\n'.join(outline))

2023-05-22 19:35:53 [info     ] requesting openai...
2023-05-22 19:36:03 [info     ] received openai...
2023-05-22 19:36:03 [info     ] Outline: ["1. Introduction of Logitech's 5-year plan", '2. Computer peripherals: expanding beyond the mouse and keyboard', '3. Gaming: the rising popularity and potential for growth', '4. Video collaboration: integrating AI for a better experience', "5. Logitech's sustainability efforts in product development", "6. The role of research and development in Logitech's plan", '7. Competing with other tech giants in the industry', '8. Looking ahead to the future of Logitech and the tech industry in general']
2023-05-22 19:36:03 [info     ] requesting openai...
2023-05-22 19:36:24 [info     ] received openai...
2023-05-22 19:36:24 [info     ] requesting tts i=0
2023-05-22 19:36:24 [info     ] requesting tts i=1
2023-05-22 19:36:24 [info     ] requesting tts i=2
2023-05-22 19:36:24 [info     ] requesting tts i=3
2023-05-22 19:36:24 [info     ] requesting tts 

2023-05-22 19:36:33 [info     ] Part: 1. Introduction of Logitech's 5-year plan
2023-05-22 19:36:33 [info     ] requesting openai...
2023-05-22 19:36:54 [info     ] received openai...
2023-05-22 19:36:54 [info     ] requesting tts i=0
2023-05-22 19:36:54 [info     ] requesting tts i=1
2023-05-22 19:36:54 [info     ] requesting tts i=2
2023-05-22 19:36:54 [info     ] requesting tts i=3
2023-05-22 19:36:54 [info     ] requesting tts i=4
2023-05-22 19:36:54 [info     ] requesting tts i=5
2023-05-22 19:36:54 [info     ] received tts i=5
2023-05-22 19:36:57 [info     ] received tts i=4
2023-05-22 19:36:57 [info     ] received tts i=2
2023-05-22 19:36:58 [info     ] received tts i=1
2023-05-22 19:36:58 [info     ] received tts i=0
2023-05-22 19:36:58 [info     ] received tts i=3
2023-05-22 19:36:58 [info     ] concatting audio
2023-05-22 19:36:58 [info     ] done with audio!


2023-05-22 19:36:58 [info     ] Part: 2. Computer peripherals: expanding beyond the mouse and keyboard
2023-05-22 19:36:58 [info     ] requesting openai...
2023-05-22 19:37:18 [info     ] received openai...
2023-05-22 19:37:18 [info     ] requesting tts i=0
2023-05-22 19:37:18 [info     ] requesting tts i=1
2023-05-22 19:37:18 [info     ] requesting tts i=2
2023-05-22 19:37:18 [info     ] requesting tts i=3
2023-05-22 19:37:18 [info     ] requesting tts i=4
2023-05-22 19:37:18 [info     ] requesting tts i=5
2023-05-22 19:37:18 [info     ] received tts i=5
2023-05-22 19:37:18 [info     ] received tts i=4
2023-05-22 19:37:21 [info     ] received tts i=3
2023-05-22 19:37:22 [info     ] received tts i=2
2023-05-22 19:37:22 [info     ] received tts i=0
2023-05-22 19:37:22 [info     ] received tts i=1
2023-05-22 19:37:22 [info     ] concatting audio
2023-05-22 19:37:22 [info     ] done with audio!


2023-05-22 19:37:22 [info     ] Part: 3. Gaming: the rising popularity and potential for growth
2023-05-22 19:37:22 [info     ] requesting openai...
2023-05-22 19:37:47 [info     ] received openai...
2023-05-22 19:37:47 [info     ] requesting tts i=0
2023-05-22 19:37:47 [info     ] requesting tts i=1
2023-05-22 19:37:47 [info     ] requesting tts i=2
2023-05-22 19:37:47 [info     ] requesting tts i=3
2023-05-22 19:37:47 [info     ] requesting tts i=4
2023-05-22 19:37:47 [info     ] requesting tts i=5
2023-05-22 19:37:47 [info     ] requesting tts i=6
2023-05-22 19:37:47 [info     ] requesting tts i=7
2023-05-22 19:37:47 [info     ] requesting tts i=8
2023-05-22 19:37:47 [info     ] received tts i=4
2023-05-22 19:37:47 [info     ] received tts i=2
2023-05-22 19:37:47 [info     ] received tts i=8
2023-05-22 19:37:48 [info     ] received tts i=7
2023-05-22 19:37:49 [info     ] received tts i=0
2023-05-22 19:37:50 [info     ] received tts i=1
2023-05-22 19:37:50 [info     ] received tts i=

2023-05-22 19:37:51 [info     ] Part: 4. Video collaboration: integrating AI for a better experience
2023-05-22 19:37:51 [info     ] requesting openai...
2023-05-22 19:38:14 [info     ] received openai...
2023-05-22 19:38:14 [info     ] requesting tts i=0
2023-05-22 19:38:14 [info     ] requesting tts i=1
2023-05-22 19:38:14 [info     ] requesting tts i=2
2023-05-22 19:38:14 [info     ] requesting tts i=3
2023-05-22 19:38:14 [info     ] requesting tts i=4
2023-05-22 19:38:14 [info     ] requesting tts i=5
2023-05-22 19:38:14 [info     ] requesting tts i=6
2023-05-22 19:38:14 [info     ] received tts i=4
2023-05-22 19:38:14 [info     ] received tts i=6
2023-05-22 19:38:17 [info     ] received tts i=1
2023-05-22 19:38:17 [info     ] received tts i=3
2023-05-22 19:38:18 [info     ] received tts i=0
2023-05-22 19:38:18 [info     ] received tts i=2
2023-05-22 19:38:19 [info     ] received tts i=5
2023-05-22 19:38:19 [info     ] concatting audio
2023-05-22 19:38:19 [info     ] done with audi

...

2023-05-22 19:38:46 [info     ] Part: 6. The role of research and development in Logitech's plan
2023-05-22 19:38:46 [info     ] Popping message: {'role': 'user', 'content': 'Generate a podcast episode about Logitechs 5 Year Plan to $10B in Revenue by Building Products in Computer Peripherals, Gaming, and Video Collaboration With AI, including history and other fun facts. Reference published scientific journals.'}
2023-05-22 19:38:46 [info     ] Popping message: {'role': 'user', 'content': "Write the intro for a podcast about Logitechs 5 Year Plan to $10B in Revenue by Building Products in Computer Peripherals, Gaming, and Video Collaboration With AI. The outline for the podcast is 1. Introduction of Logitech's 5-year plan, 2. Computer peripherals: expanding beyond the mouse and keyboard, 3. Gaming: the rising popularity and potential for growth, 4. Video collaboration: integrating AI for a better experience, 5. Logitech's sustainability efforts in product development, 6. The role of r

2023-05-22 19:39:11 [info     ] Part: 7. Competing with other tech giants in the industry
2023-05-22 19:39:11 [info     ] Popping message: {'role': 'assistant', 'content': "Tom: Hey there listeners and welcome back to our award-winning NPR podcast. In today's episode, we're diving into the world of Logitech - the Swiss-based company that designs and manufactures computer peripherals, gaming accessories, and video collaboration tools. By 2025, Logitech has a bold plan to reach $10 billion in revenue by building innovative products that integrate AI and sustainability. \n\nJen: That's right, Tom. Logitech is a fascinating company with a rich history. Did you know it was founded in 1981 in Switzerland? It all started when Daniel Borel, Pierluigi Zappacosta, and Giacomo Marini wanted to make personal computers easier to use. \n\nTom: Absolutely, Jen. And over the years, Logitech has become synonymous with computer mice and keyboards, but their 5-year plan is aiming to expand far beyond tha

2023-05-22 19:39:43 [info     ] Part: 8. Looking ahead to the future of Logitech and the tech industry in general
2023-05-22 19:39:43 [info     ] Popping message: {'role': 'user', 'content': "Write the next part: 1. Introduction of Logitech's 5-year plan. Remember to respond with the hosts names like Tom: and Jen:"}
2023-05-22 19:39:43 [info     ] Popping message: {'role': 'assistant', 'content': "Jen: Logitech's 5-year plan is focused on expanding their product offerings in three main areas - computer peripherals, gaming, and video collaboration. By investing in AI and sustainability, they hope to double their revenue by 2025. \n\nTom: That's right, Jen. And it all starts with computer peripherals - a space Logitech has been a major player in for decades. But what's interesting is that they're now looking beyond traditional accessories like mice and keyboards and exploring new product categories. \n\nJen: In fact, Logitech has already launched several new products, like their presenta

2023-05-22 19:40:10 [info     ] Conclusion
2023-05-22 19:40:10 [info     ] Popping message: {'role': 'user', 'content': 'Write the next part: 2. Computer peripherals: expanding beyond the mouse and keyboard. Remember to respond with the hosts names like Tom: and Jen:'}
2023-05-22 19:40:10 [info     ] Popping message: {'role': 'assistant', 'content': "Jen: Logitech's expansion plans in computer peripherals go beyond just launching new products. They're also looking to create a more seamless user experience by integrating AI into their devices. \n\nTom: That's right, Jen. Logitech is exploring how AI can be used to personalize and optimize how their products work. For example, their software can already detect when you're using a mouse and adjust the cursor sensitivity accordingly. \n\nJen: And they're working on incorporating AI into other product lines, like their webcams and keyboards. By doing this, they're creating a more intuitive and customized experience for users. \n\nTom: It's 

CPU times: user 2.59 s, sys: 720 ms, total: 3.31 s
Wall time: 4min 41s


In [ ]:
"""
TODO:
    - runtime voice choosing to include accented voices
"""

In [ ]:
"""
TODO:
    Make web server and send mp3 to frontend
    Make frontend and play results
"""